In [11]:
%load_ext autoreload

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [12]:
%autoreload 2

In [13]:
%matplotlib inline
import sys
sys.path.append('../')
import RNA 
from utils.sequence_utils import generate_random_mutant
from utils.model_architectures import Linear, NLNN, CNNa
from models.Noisy_models.Neural_network_models import NN_model
from models.Ground_truth_oracles.RNA_landscape_models import RNA_landscape_constructor
from models.Noisy_models.Ensemble import Ensemble_models
from evaluators.Evaluator import Evaluator
from models.Ground_truth_oracles.TF_binding_landscape_models import *

LANDSCAPE_TYPES ={"RNA": [0, 1], 'TF':['SIX6_REF_R1']} # for testing 
mutation_rate = 0.5
RNA_alphabet = "UCGA" 
DNA_alphabet = "TCGA"
landscape_constructor = RNA_landscape_constructor()
#load a pre-specified landscapes  (here, index 0), you can also specify to just take a few of them
landscape_constructor.load_landscapes("../data/RNA_landscapes/RNA_landscape_config.yaml", landscapes_to_test=[0])
landscape_generator = landscape_constructor.generate_from_loaded_landscapes()
landscape_object=next(landscape_generator)
wt = landscape_object['starting_seqs']['startRNAL14_3']
landscape_oracle = landscape_object['landscape_oracle']

training_sequences = [wt]
cnn_architecture=CNNa(len(wt), alphabet=RNA_alphabet)
noisy_nn_model=NN_model(landscape_oracle, cnn_architecture)
noisy_nn_model.reset()
noisy_nn_model.update_model(training_sequences)

B1L14RNA1 loaded


/home/alexander/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_regression.py:582: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)


## DQN Explorer

In [14]:
from explorers.dqn_explorer import DQN_Explorer 

num_of_rounds = 5

# reset model if it already exists 
training_sequences = [wt]
cnn_architecture=CNNa(len(wt), alphabet=RNA_alphabet)
noisy_nn_model=NN_model(landscape_oracle, cnn_architecture)
noisy_nn_model.reset()
noisy_nn_model.update_model(training_sequences)

# evaluate DQN Explorer 
dqn_explorer = DQN_Explorer(train_epochs=10)
dqn_explorer.debug = True
dqn_explorer.set_model(noisy_nn_model)
dqn_explorer.run(num_of_rounds, verbose=True)

/home/alexander/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_regression.py:582: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)


round: 0, cost: 1, evals: 0, top: 0.14554841726711917
round: 1, cost: 101, evals: 883, top: 0.5794474621391882
round: 2, cost: 201, evals: 1674, top: 0.7085186640203461
round: 3, cost: 301, evals: 2423, top: 0.741473042412728
round: 4, cost: 401, evals: 2965, top: 0.741473042412728


In [15]:
landscape_constructor=TF_binding_landscape_constructor()
landscape_constructor.load_landscapes(landscapes_to_test = ['SIX6_REF_R1'])
landscape_generator = landscape_constructor.generate_from_loaded_landscapes()
landscape_object = next(landscape_generator)
wt = landscape_object['starting_seqs']['TF0']
landscape_oracle = landscape_object['landscape_oracle']

# reset model if it already exists 
training_sequences = [wt]
cnn_architecture=CNNa(len(wt), alphabet=DNA_alphabet)
noisy_nn_model=NN_model(landscape_oracle, cnn_architecture)
noisy_nn_model.reset()
noisy_nn_model.update_model(training_sequences)

# evaluate DQN Explorer 
dqn_explorer = DQN_Explorer(alphabet=DNA_alphabet, train_epochs=10, virtual_screen=20)
dqn_explorer.debug = True
dqn_explorer.set_model(noisy_nn_model)
dqn_explorer.run(num_of_rounds, verbose=True)

1 TF landscapes loaded.


/home/alexander/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_regression.py:582: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)


round: 0, cost: 1, evals: 0, top: 0.6781429101554447
round: 1, cost: 1, evals: 0, top: 0.6781429101554447
round: 2, cost: 1, evals: 0, top: 0.6781429101554447
round: 3, cost: 1, evals: 0, top: 0.6781429101554447
round: 4, cost: 1, evals: 0, top: 0.6781429101554447


In [18]:
from explorers.dqn_explorer import DQN_Explorer 

dqn_explorer_prod = DQN_Explorer(train_epochs=10)
dqn_explorer_prod.debug = False

In [ ]:
# run all evaluations 
evaluator_dqn=Evaluator(dqn_explorer_prod,landscape_types=LANDSCAPE_TYPES, path="../simulations/eval/")
evaluator_dqn.evaluate_for_landscapes(evaluator_dqn.adaptivity, num_starts=3)
evaluator_dqn=Evaluator(dqn_explorer_prod,landscape_types=LANDSCAPE_TYPES, path="../simulations/eval/")
evaluator_dqn.evaluate_for_landscapes(evaluator_dqn.efficiency, num_starts=3)
evaluator_dqn=Evaluator(dqn_explorer_prod,landscape_types=LANDSCAPE_TYPES, path="../simulations/eval/")
evaluator_dqn.evaluate_for_landscapes(evaluator_dqn.scalability, num_starts=3)

In [19]:
evaluator_dqn=Evaluator(dqn_explorer_prod,landscape_types=LANDSCAPE_TYPES, path="../simulations/eval/")
evaluator_dqn.evaluate_for_landscapes(evaluator_dqn.consistency_robustness_independence, num_starts=3)

loading landscapes RNA: [0, 1], TF:['SIX6_REF_R1']
B1L14RNA1 loaded
B1L50RNA1 loaded
1 TF landscapes loaded.
loading complete
Running on B1L14RNA1
start seq startRNAL14_0
round: 0, cost: 1, evals: 0, top: 0.5437468768175177
round: 1, cost: 101, evals: 852, top: 0.6645795626698909
round: 2, cost: 201, evals: 1132, top: 0.6645795626698909
round: 3, cost: 201, evals: 1132, top: 0.6645795626698909
round: 4, cost: 201, evals: 1132, top: 0.6645795626698909
round: 5, cost: 201, evals: 1132, top: 0.6645795626698909
round: 6, cost: 201, evals: 1132, top: 0.6645795626698909
round: 7, cost: 201, evals: 1132, top: 0.6645795626698909
round: 8, cost: 201, evals: 1132, top: 0.6645795626698909
round: 9, cost: 201, evals: 1132, top: 0.6645795626698909
round: 0, cost: 1, evals: 0, top: 0.5437468768175177
round: 1, cost: 1, evals: 0, top: 0.5437468768175177
round: 2, cost: 1, evals: 0, top: 0.5437468768175177
round: 3, cost: 1, evals: 0, top: 0.5437468768175177
round: 4, cost: 1, evals: 0, top: 0.5437468

/home/alexander/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_regression.py:582: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
/home/alexander/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_regression.py:582: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
/home/alexander/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_regression.py:582: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
/home/alexander/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_regression.py:582: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
/home/alexander/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_regression.py:582: UndefinedMetricWarning: R^2 score is not w

round: 0, cost: 1, evals: 0.0, top: 0.5437468768175177
round: 1, cost: 1, evals: 0.0, top: 0.5437468768175177
round: 2, cost: 1, evals: 0.0, top: 0.5437468768175177
round: 3, cost: 1, evals: 0.0, top: 0.5437468768175177
round: 4, cost: 1, evals: 0.0, top: 0.5437468768175177
round: 5, cost: 1, evals: 0.0, top: 0.5437468768175177
round: 6, cost: 1, evals: 0.0, top: 0.5437468768175177
round: 7, cost: 1, evals: 0.0, top: 0.5437468768175177
round: 8, cost: 1, evals: 0.0, top: 0.5437468768175177
round: 9, cost: 1, evals: 0.0, top: 0.5437468768175177


/home/alexander/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_regression.py:582: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
/home/alexander/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_regression.py:582: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
/home/alexander/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_regression.py:582: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
/home/alexander/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_regression.py:582: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
/home/alexander/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_regression.py:582: UndefinedMetricWarning: R^2 score is not w

round: 0, cost: 1, evals: 0.0, top: 0.5437468768175177
round: 1, cost: 1, evals: 0.0, top: 0.5437468768175177
round: 2, cost: 1, evals: 0.0, top: 0.5437468768175177
round: 3, cost: 1, evals: 0.0, top: 0.5437468768175177
round: 4, cost: 1, evals: 0.0, top: 0.5437468768175177
round: 5, cost: 1, evals: 0.0, top: 0.5437468768175177
round: 6, cost: 1, evals: 0.0, top: 0.5437468768175177
round: 7, cost: 1, evals: 0.0, top: 0.5437468768175177
round: 8, cost: 1, evals: 0.0, top: 0.5437468768175177
round: 9, cost: 1, evals: 0.0, top: 0.5437468768175177


...

round: 0, cost: 1, evals: 0.0, top: 0.33058796849874245
round: 1, cost: 1, evals: 0.0, top: 0.33058796849874245
round: 2, cost: 1, evals: 0.0, top: 0.33058796849874245
round: 3, cost: 1, evals: 0.0, top: 0.33058796849874245
round: 4, cost: 1, evals: 0.0, top: 0.33058796849874245
round: 5, cost: 1, evals: 0.0, top: 0.33058796849874245
round: 6, cost: 1, evals: 0.0, top: 0.33058796849874245
round: 7, cost: 1, evals: 0.0, top: 0.33058796849874245
round: 8, cost: 1, evals: 0.0, top: 0.33058796849874245
round: 9, cost: 1, evals: 0.0, top: 0.33058796849874245


/home/alexander/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_regression.py:582: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
/home/alexander/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_regression.py:582: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
/home/alexander/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_regression.py:582: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
/home/alexander/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_regression.py:582: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
/home/alexander/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_regression.py:582: UndefinedMetricWarning: R^2 score is not w

round: 0, cost: 1, evals: 0.0, top: 0.33058796849874245
round: 1, cost: 1, evals: 0.0, top: 0.33058796849874245
round: 2, cost: 1, evals: 0.0, top: 0.33058796849874245
round: 3, cost: 1, evals: 0.0, top: 0.33058796849874245
round: 4, cost: 1, evals: 0.0, top: 0.33058796849874245
round: 5, cost: 1, evals: 0.0, top: 0.33058796849874245
round: 6, cost: 1, evals: 0.0, top: 0.33058796849874245
round: 7, cost: 1, evals: 0.0, top: 0.33058796849874245
round: 8, cost: 1, evals: 0.0, top: 0.33058796849874245
round: 9, cost: 1, evals: 0.0, top: 0.33058796849874245


/home/alexander/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_regression.py:582: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
/home/alexander/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_regression.py:582: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
/home/alexander/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_regression.py:582: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
/home/alexander/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_regression.py:582: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
/home/alexander/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_regression.py:582: UndefinedMetricWarning: R^2 score is not w

round: 0, cost: 1, evals: 0.0, top: 0.33058796849874245
round: 1, cost: 1, evals: 0.0, top: 0.33058796849874245
round: 2, cost: 1, evals: 0.0, top: 0.33058796849874245
round: 3, cost: 1, evals: 0.0, top: 0.33058796849874245
round: 4, cost: 1, evals: 0.0, top: 0.33058796849874245
round: 5, cost: 1, evals: 0.0, top: 0.33058796849874245
round: 6, cost: 1, evals: 0.0, top: 0.33058796849874245
round: 7, cost: 1, evals: 0.0, top: 0.33058796849874245
round: 8, cost: 1, evals: 0.0, top: 0.33058796849874245
round: 9, cost: 1, evals: 0.0, top: 0.33058796849874245
round: 0, cost: 1, evals: 0, top: 0.33058796849874245
round: 1, cost: 101, evals: 722, top: 0.8593576052447119
round: 2, cost: 200, evals: 1325, top: 0.8911681029151033
round: 3, cost: 299, evals: 1873, top: 0.9717045313981776
round: 4, cost: 399, evals: 2209, top: 0.9717045313981776
round: 5, cost: 497, evals: 2354, top: 0.9717045313981776
round: 6, cost: 584, evals: 2534, top: 0.9717045313981776
round: 7, cost: 672, evals: 2700, top: 

## BO Explorer

In [ ]:
%autoreload 2
from explorers.bo_explorer import BO_Explorer

num_of_rounds = 5
arch1 = NLNN(len(wt), hidden_dims=10, epochs=20)
arch2 = NLNN(len(wt), hidden_dims=20, epochs=20)
arch3 = NLNN(len(wt), hidden_dims=30, epochs=20)
arch4 = NLNN(len(wt), hidden_dims=40, epochs=20)
# ensemble we will use for BO Explorer
nn_model_1 = NN_model(landscape_oracle, arch1)
nn_model_2 = NN_model(landscape_oracle, arch2)
nn_model_3 = NN_model(landscape_oracle, arch3)
nn_model_4 = NN_model(landscape_oracle, arch4)
models = [nn_model_1, nn_model_2, nn_model_3, nn_model_4]
ensemble_model = Ensemble_models(models)
ensemble_model.update_model(training_sequences)

In [ ]:
# evaluate BO Explorer 
bo_explorer = BO_Explorer()
bo_explorer.debug = True
bo_explorer.set_model(ensemble_model)
bo_explorer.run(num_of_rounds, verbose=True)

In [20]:
from explorers.bo_explorer import BO_Explorer

bo_explorer_prod = BO_Explorer()
bo_explorer_prod.debug = False

In [ ]:
# run all evaluations 
evaluator_bo=Evaluator(bo_explorer_prod,landscape_types=LANDSCAPE_TYPES, path="../simulations/eval/")
evaluator_bo.evaluate_for_landscapes(evaluator_bo.adaptivity, num_starts=3)
evaluator_bo=Evaluator(bo_explorer_prod,landscape_types=LANDSCAPE_TYPES, path="../simulations/eval/")
evaluator_bo.evaluate_for_landscapes(evaluator_bo.efficiency, num_starts=3)
evaluator_bo=Evaluator(bo_explorer_prod,landscape_types=LANDSCAPE_TYPES, path="../simulations/eval/")
evaluator_bo.evaluate_for_landscapes(evaluator_bo.scalability, num_starts=3)

In [21]:
evaluator_bo=Evaluator(bo_explorer_prod,landscape_types=LANDSCAPE_TYPES, path="../simulations/eval/")
evaluator_bo.evaluate_for_landscapes(evaluator_bo.consistency_robustness_independence, num_starts=3)

loading landscapes RNA: [0, 1], TF:['SIX6_REF_R1']
B1L14RNA1 loaded
B1L50RNA1 loaded
1 TF landscapes loaded.
loading complete
Running on B1L14RNA1
start seq startRNAL14_0
round: 0, cost: 1, evals: 0, top: 0.5437468768175177


../models/Ground_truth_oracles/RNA_landscape_models.py:21: YAMLLoadWarning: calling yaml.load() without Loader=... is deprecated, as the default Loader is unsafe. Please read https://msg.pyyaml.org/load for full details.
  self.loaded_landscapes = yaml.load(cfgfile)


round: 1, cost: 11, evals: 399, top: 0.5492392906760948
round: 2, cost: 20, evals: 800, top: 0.5492392906760948
round: 3, cost: 30, evals: 1201, top: 0.5492392906760948
round: 4, cost: 42, evals: 1601, top: 0.5492392906760948
round: 5, cost: 54, evals: 2002, top: 0.5492392906760948
round: 6, cost: 68, evals: 2402, top: 0.5492392906760948
round: 7, cost: 75, evals: 2803, top: 0.6343713912067976
round: 8, cost: 84, evals: 3204, top: 0.6343713912067976
round: 9, cost: 94, evals: 3604, top: 0.6343713912067976
round: 0, cost: 1, evals: 0, top: 0.5437468768175177
round: 1, cost: 13, evals: 397, top: 0.5437468768175177
round: 2, cost: 24, evals: 796, top: 0.5437468768175177
round: 3, cost: 29, evals: 1197, top: 0.5437468768175177
round: 4, cost: 41, evals: 1598, top: 0.5437468768175177
round: 5, cost: 53, evals: 1999, top: 0.5437468768175177
round: 6, cost: 64, evals: 2399, top: 0.5849398236182248
round: 7, cost: 75, evals: 2800, top: 0.5849398236182248
round: 8, cost: 88, evals: 3201, top: 0

/home/alexander/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_regression.py:582: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
/home/alexander/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_regression.py:582: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
/home/alexander/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_regression.py:582: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
/home/alexander/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_regression.py:582: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
/home/alexander/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_regression.py:582: UndefinedMetricWarning: R^2 score is not w

round: 0, cost: 1, evals: 0.0, top: 0.5437468768175177


...

round: 9, cost: 93, evals: 3592.0, top: 0.921875644250196


/home/alexander/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_regression.py:582: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
/home/alexander/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_regression.py:582: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
/home/alexander/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_regression.py:582: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
/home/alexander/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_regression.py:582: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
/home/alexander/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_regression.py:582: UndefinedMetricWarning: R^2 score is not w

/home/alexander/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_regression.py:582: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
/home/alexander/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_regression.py:582: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
/home/alexander/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_regression.py:582: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
/home/alexander/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_regression.py:582: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
/home/alexander/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_regression.py:582: UndefinedMetricWarning: R^2 score is not w

/home/alexander/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_regression.py:582: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
/home/alexander/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_regression.py:582: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
/home/alexander/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_regression.py:582: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
/home/alexander/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_regression.py:582: UndefinedMetricWarning: R^2 score is not well-defined with less than two samples.
  warnings.warn(msg, UndefinedMetricWarning)
/home/alexander/anaconda3/lib/python3.7/site-packages/sklearn/metrics/_regression.py:582: UndefinedMetricWarning: R^2 score is not w

round: 0, cost: 1, evals: 0, top: 0.33058796849874245
round: 1, cost: 12, evals: 396, top: 0.8691295922153961
round: 2, cost: 21, evals: 794, top: 0.8691295922153961
round: 3, cost: 32, evals: 1193, top: 0.8691295922153961
round: 4, cost: 36, evals: 1594, top: 0.8691295922153961
round: 5, cost: 49, evals: 1994, top: 0.8691295922153961
round: 6, cost: 59, evals: 2392, top: 0.8691295922153961
round: 7, cost: 73, evals: 2793, top: 0.8691295922153961
round: 8, cost: 82, evals: 3194, top: 0.8691295922153961
round: 9, cost: 93, evals: 3595, top: 0.9148146621036574
